# [Su Doku](https://projecteuler.net/problem=96)

This problem can be solved by hand!

... as long as you like [Sudoku](https://en.wikipedia.org/wiki/Sudoku) and have some time to kill. (Sudoku is fun, so this isn't a crazy idea - [here are some solving strategies](https://www.sudokuwiki.org/Getting_Started).)

As with many problems before, SageMath makes this trivially easy - [it has a Sudoku solver built in](https://doc.sagemath.org/html/en/reference/games/sage/games/sudoku.html). All we really need to do is the tedious part: reading the file with all the puzzles.

In [1]:
rows = []
with open("txt/p096_sudoku.txt") as f:
    for line in f:
        if not line.startswith("Grid"):
            rows.append([int(n) for n in line.strip()])

grids = [matrix(rows[i:i+9]) for i in range(0, 50*9, 9)]

Here's the first puzzle again.

In [2]:
puzzles = [Sudoku(grid) for grid in grids]
puzzles[0]

+-----+-----+-----+
|    3|  2  |6    |
|9    |3   5|    1|
|    1|8   6|4    |
+-----+-----+-----+
|    8|1   2|9    |
|7    |     |    8|
|    6|7   8|2    |
+-----+-----+-----+
|    2|6   9|5    |
|8    |2   3|    9|
|    5|  1  |3    |
+-----+-----+-----+

Here's SageMath solving it, and the 49 other puzzles:

In [3]:
solutions = [next(puzzle.solve()) for puzzle in puzzles]

And now we sum up the numbers in the top-left corner:

In [4]:
first_three_digit_num = lambda s: int(s.to_string()[0:3])
sum(first_three_digit_num(s) for s in solutions)

24702

Done!

But of course, we should talk about what SageMath is actually *doing*. 

Sudoku falls under the broad category of [constraint satisfaction problems](https://en.wikipedia.org/wiki/Constraint_satisfaction_problem). In general, these are hard to solve efficiently, but a standard 9x9 Sudoku grid isn't too bad.

There are [many algorithms for solving Sudoku](https://en.wikipedia.org/wiki/Sudoku_solving_algorithms), and SageMath has two at its disposal. We'll also look at a more mathematical approach to understanding the problem.

## Backtracking
The backtracking approach is fundamentally a [depth-first search](https://en.wikipedia.org/wiki/Depth-first_search) of the "search tree" of possible Sudoku grids. All you do is iterate through every open cell in the grid and try every possible number for the current cell. We make a copy of the grid for each possible guess and continue to the next open cell for each copy. If no numbers 1-9 work, an earlier guess was wrong, so we "backtrack" to make a different guess. [Here's a nice gif visualization](https://commons.wikimedia.org/wiki/File:Sudoku_solved_by_bactracking.gif).

To make it easier to index the boxes of our Sudoku puzzles, we'll subdivide our matrices into 3x3 submatrices.

In [5]:
for grid in grids:
    grid.subdivide([3,6], [3,6])

Here's a visualization. As a bonus, it looks more like a Sudoku grid this way.

In [6]:
grids[0]

[0 0 3|0 2 0|6 0 0]
[9 0 0|3 0 5|0 0 1]
[0 0 1|8 0 6|4 0 0]
[-----+-----+-----]
[0 0 8|1 0 2|9 0 0]
[7 0 0|0 0 0|0 0 8]
[0 0 6|7 0 8|2 0 0]
[-----+-----+-----]
[0 0 2|6 0 9|5 0 0]
[8 0 0|2 0 3|0 0 9]
[0 0 5|0 1 0|3 0 0]

And here's where we apply depth-first search to solve. Once we have a valid grid with all the cells filled in, we're done!

In [7]:
from itertools import product

def solve(grid):
    positions = set(product(*(range(k) for k in grid.dimensions())))
    
    stack = [grid]
    while stack != []:
        g = stack.pop()
            
        nonzero_positions = set(g.nonzero_positions())
        if len(nonzero_positions) == prod(g.dimensions()):
            break
        
        # get the first empty cell
        zero_positions = sorted(positions - nonzero_positions)
        i, j = zero_positions[0]
        
        box = g.subdivision(i // 3, j // 3)
        candidates = set(range(1, 10)) - set(g.row(i)) - set(g.column(j)) - set(box.list())
        for c in candidates:
            h = matrix(g)
            h[i, j] = c
            stack.append(h)
        
    return g

Here's the solution to the first grid again.

In [8]:
solve(grids[0])

[4 8 3|9 2 1|6 5 7]
[9 6 7|3 4 5|8 2 1]
[2 5 1|8 7 6|4 9 3]
[-----+-----+-----]
[5 4 8|1 3 2|9 7 6]
[7 2 9|5 6 4|1 3 8]
[1 3 6|7 9 8|2 4 5]
[-----+-----+-----]
[3 7 2|6 8 9|5 1 4]
[8 1 4|2 5 3|7 6 9]
[6 9 5|4 1 7|3 8 2]

*Note that this is a pretty slow implementation of backtracking.*

The downside of this method is that if you make a bad guess early on, it might not be until much later that the grid is found to be invalid, so there will be a lot of backtracking before you can correct the first bad guess.

The backtracking method is available to SageMath's built-in Sudoku solver, but it's not what it uses by default.

## Graph theory

Another way to approach solving Sudoku is to frame it as a graph theory problem.

A Sudoku puzzle can be modeled as a [Sudoku graph](https://en.wikipedia.org/wiki/Sudoku_graph), which is a [20-regular graph](https://en.wikipedia.org/wiki/Regular_graph) where each vertex represents one of the puzzle's cells, and there's an edge between every pair of vertices that lie in the same row, column, or box. Just as the goal in the original puzzle is to put numbers in each cell so no number appears more than once in each row, column, or box, the goal in the graph formulation is to label each vertex so no two vertices with the same label are connected by an edge. If we just substitute number labels for colors, then this is analogous to a [graph coloring](https://en.wikipedia.org/wiki/Graph_coloring) problem. Specifically, it is a [precoloring extension](https://en.wikipedia.org/wiki/Precoloring_extension), since some cells (vertices) are initially assigned numbers (colors).

I just mention this as a fun alternate way to think about Sudoku - this isn't how SageMath solves Sudoku puzzles.

## Exact cover problem
Yet another way to approach solving a Sudoku puzzle is to formulate it as an [exact cover](https://en.wikipedia.org/wiki/Exact_cover) problem. Put succinctly, given a set $X$ and another set $S$ composed of subsets of $X$, the problem is to find $S^* \subseteq S$ such that $S^*$ is a [partition](https://en.wikipedia.org/wiki/Partition_of_a_set) of $X$, if one exists.

To formulate Sudoku as an exact cover problem, first consider how there are $9 \times 9 = 81$ cells that can each hold any number 1 through 9. This totals to 729 options for filling in the grid's cells.

Obviously, though, there are constraints imposed. I think the easiest way to think about the constraints is to list them. First, we have a (seemingly trivial, but nonetheless important) constraint on each cell:
1. Cell (1, 1) must have a number
2. Cell (1, 2) must have a number
3. Cell (1, 3) must have a number

... and so on, 81 times.

After this, there are constraints on the rows:
1. Row 1 must have a 1
2. Row 1 must have a 2
3. Row 1 must have a 3

... and so on, for each number 1 through 9 and for each of the 9 rows. This results in another 81 constraints a solved board must satisfy.

Similarly, there 81 more constraints imposed by each *column* needing to contain 1 through 9 exactly once, and 81 more constraints imposed by each *box* needing to contain 1 through 9 exactly once. This gives a grand total of 324 constraints that a valid Sudoku board must satisfy.

Each of the 729 options for filling the cells will satisfy four of these constraints at a time (i.e. each time we fill in a cell, we satisfy one of each of the cell, row, column, and box constraints). To represent which constraints are satisfied, we can write each option as an array of 324 booleans, four of which are 1.

We now have a model of the Sudoku board as a $729 \times 324$ binary matrix - [here's a surprisingly readable rendering of it](https://www.stolaf.edu/people/hansonr/sudoku/exactcovermatrix.htm). To solve the puzzle, we want to select 81 rows of this matrix that, together, satisfy each one of the 324 constraints *exactly once* (if any of the constraints were satisfied more than once, that would imply we have the same number appearing more than once in one row/column/box, or that one cell has multiple numbers).

To go back to our more formal definition of the exact cover problem:
* $X$ is a set of 324 constraints.
* $S$ is a set of 729 distinct subsets of $X$.
* The goal is to select a subset of $S$ that forms a partition of $X$.

Since a Sudoku puzzle starts with some cells filled in, certain elements of $S$ will be required in our solution for a given puzzle.

### Algorithm X and dancing links
[Knuth's Algorithm X](https://en.wikipedia.org/wiki/Knuth%27s_Algorithm_X) is a backtracking algorithm for the exact cover problem.

Algorithm X can be made more efficient by applying a property Knuth named [dancing links](https://en.wikipedia.org/wiki/Dancing_Links). This concept boils down to the fact you can efficiently re-add a previously removed node to a [doubly linked list](https://en.wikipedia.org/wiki/Doubly_linked_list).

By creating a special data structure ([shown here](https://commons.wikimedia.org/wiki/File:Dancing_links.svg)) that takes advantage of this property, you can create a very efficient implementation of Algorithm X. Such an implementation is deemed DLX, and *this* is the default algorithm that SageMath uses in its Sudoku solver.